In [ ]:
# Module 2 - Create a Cryptocurrency

# To be installed:
# Flask==0.12.2: pip install Flask==0.12.2
# Postman HTTP Client: https://www.getpostman.com/
# requests==2.18.4: pip install requests==2.18.4

# Importing the libraries
import json
from flask import Flask, jsonify, request
import requests
from uuid import uuid4
from urllib.parse import urlparse
import os
import pandas as pd 
import numpy as np 

from keras.models import load_model
import cv2
import numpy as np
import os
from matplotlib import pyplot as plt
import time
import imutils
import mediapipe as mp




mp_holistic = mp.solutions.holistic # Holistic model
mp_drawing = mp.solutions.drawing_utils # Drawing utilities
mp_hands = mp.solutions.hands
modelpsl = load_model('action.h5')
modelAtOZ = load_model('actionAtoz.h5')
actions = np.array(['Now', 'What', 'Before', 'Birthday', 'Capital', 'Child', 'Time', 'Drink', 'Education', 'Food', 'Friend', 'Good', 'Happy', 'Hello','Job','Market', 'Mother', 'Pakistan','Restaurant', 'Tahnk you'])
actions2 = np.array(['A','B', 'C','D','E','F', 'G','H','I', 'K','L','M', 'N', 'O','P','Q','R','S', 'T', 'U','V', 'W', 'X', 'Z'])
def mediapipe_detection(image, model):
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB) # COLOR CONVERSION BGR 2 RGB
    image.flags.writeable = False                  # Image is no longer writeable
    results = model.process(image)                 # Make prediction
    image.flags.writeable = True                   # Image is now writeable 
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR) # COLOR COVERSION RGB 2 BGR
    return image, results

def draw_landmarks2(image, results):
    #mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS) # Draw face connections
    #mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS) # Draw pose connections
  
            for num, hand in enumerate(results.multi_hand_landmarks):
                mp_drawing.draw_landmarks(image, hand, mp_hands.HAND_CONNECTIONS, 
                                        mp_drawing.DrawingSpec(color=(121, 22, 76), thickness=2, circle_radius=4),
                                        mp_drawing.DrawingSpec(color=(250, 44, 250), thickness=2, circle_radius=2),
                                         )

def draw_landmarks(image, results):
    mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS) # Draw face connections
    mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS) # Draw pose connections
    mp_drawing.draw_landmarks(image, results.left_hand_landmarks, mp_holistic.HAND_CONNECTIONS) # Draw left hand connections
    mp_drawing.draw_landmarks(image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS) # Draw right hand connections
    



def draw_styled_landmarks(image, results):
    # Draw face connections
    mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS, 
                             mp_drawing.DrawingSpec(color=(80,110,10), thickness=1, circle_radius=1), 
                             mp_drawing.DrawingSpec(color=(80,256,121), thickness=1, circle_radius=1)
                             ) 
    # Draw pose connections
    mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS,
                             mp_drawing.DrawingSpec(color=(80,22,10), thickness=2, circle_radius=4), 
                             mp_drawing.DrawingSpec(color=(80,44,121), thickness=2, circle_radius=2)
                             ) 
    # Draw left hand connections
    mp_drawing.draw_landmarks(image, results.left_hand_landmarks, mp_holistic.HAND_CONNECTIONS, 
                             mp_drawing.DrawingSpec(color=(121,22,76), thickness=2, circle_radius=4), 
                             mp_drawing.DrawingSpec(color=(121,44,250), thickness=2, circle_radius=2)
                             ) 
    # Draw right hand connections  
    mp_drawing.draw_landmarks(image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS, 
                             mp_drawing.DrawingSpec(color=(245,117,66), thickness=2, circle_radius=4), 
                             mp_drawing.DrawingSpec(color=(245,66,230), thickness=2, circle_radius=2)
                             ) 
    
def draw_styled_landmarks2(image, results):
    # Draw face connections
   # mp_drawing.draw_landmarks(image, results.face_landmarks, mp_holistic.FACE_CONNECTIONS, 
                             #mp_drawing.DrawingSpec(color=(80,110,10), thickness=1, circle_radius=1), 
                             #mp_drawing.DrawingSpec(color=(80,256,121), thickness=1, circle_radius=1)
                             #) 
    # Draw pose connections
    #mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_holistic.POSE_CONNECTIONS,
                             #mp_drawing.DrawingSpec(color=(80,22,10), thickness=2, circle_radius=4), 
                             #mp_drawing.DrawingSpec(color=(80,44,121), thickness=2, circle_radius=2)
                           #  ) 
    # Draw left hand connections
       if results.multi_hand_landmarks:
            for num, hand in enumerate(results.multi_hand_landmarks):
                mp_drawing.draw_landmarks(image, hand, mp_hands.HAND_CONNECTIONS, 
                                        mp_drawing.DrawingSpec(color=(121, 22, 76), thickness=2, circle_radius=4),
                                        mp_drawing.DrawingSpec(color=(250, 44, 250), thickness=2, circle_radius=2),
                                         )
    # Draw right hand connections  
    #mp_drawing.draw_landmarks(image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS, 
                             #mp_drawing.DrawingSpec(color=(245,117,66), thickness=2, circle_radius=4), 
                             #mp_drawing.DrawingSpec(color=(245,66,230), thickness=2, circle_radius=2)
                            # )     
    

def extract_keypoints(results):
    pose = np.array([[res.x, res.y, res.z, res.visibility] for res in results.pose_landmarks.landmark]).flatten() if results.pose_landmarks else np.zeros(33*4)
    face = np.array([[res.x, res.y, res.z] for res in results.face_landmarks.landmark]).flatten() if results.face_landmarks else np.zeros(468*3)
    lh = np.array([[res.x, res.y, res.z] for res in results.left_hand_landmarks.landmark]).flatten() if results.left_hand_landmarks else np.zeros(21*3)
    rh = np.array([[res.x, res.y, res.z] for res in results.right_hand_landmarks.landmark]).flatten() if results.right_hand_landmarks else np.zeros(21*3)
    return np.concatenate([pose, lh, rh])


def extract_keypoints2(results):
    hand = np.array([[[res.x, res.y, res.z] for res in rest.landmark]for rest in results.multi_hand_landmarks]).flatten() if results.multi_hand_landmarks else np.zeros(21*3);
    return hand
    
def ValuePredictor(path):
    sequence = []
    sentence = []
    predictions = []
    threshold = 0.8
    print(path)
    cap = cv2.VideoCapture(str(path))
    with mp_holistic.Holistic(min_detection_confidence=0.5, min_tracking_confidence=0.5) as holistic: 
        sequence = []
        for seq in range(3):
            # Loop through video length aka sequence length
            for frame_num in range(50):

                # Read feed
                ret, frame = cap.read()
                if ret==True:
                # Make detections
                    frame= imutils.resize(frame, width=920, height=920)
                    image, results = mediapipe_detection(frame, holistic)
                    #print(image)

                    # Draw landmarks
                    draw_styled_landmarks(image, results)

                    # NEW Apply wait logic
                    if frame_num == 0: 
                        cv2.rectangle(image, (0,0), (640, 40), (245, 117, 16), -1)
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32), 
                                                           cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)

                    # Show to screenq
                        cv2.imshow('OpenCV Feed', image)
                        #cv2.waitKey(1000)
                    else: 
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32),cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                        # Show to screen
                        cv2.imshow('OpenCV Feed', image)

                    # NEW Export keypoints
                    #print(results.multi_hand_landmarks)
                    keypoints = extract_keypoints(results)
                    print(keypoints)
                    npy_path = os.path.join('test', str(seq))
                    np.save(npy_path, keypoints)

                    # Break gracefully
                    if cv2.waitKey(15) & 0xFF == ord('q'):
                        break

    cap.release()
    cv2.destroyAllWindows()
    for frame_num in range(3):
        res = np.load(os.path.join('test', "{}.npy".format(frame_num)))
        #print(np.array(res).size)
        sequence.append(res)
        print(res)
        #print(window)

    #print(sequences)

    res = modelpsl.predict(np.expand_dims(sequence, axis=0))[0]
    print(actions[np.argmax(res)])
    predictions.append(np.argmax(res))
    return actions[np.argmax(res)]




def ValuePredictor2(path):
    sequence = []
    sentence = []
    predictions = []
    threshold = 0.8
    #print('hellooo')
    #print(path)
    cap = cv2.VideoCapture(str(path))
    #print(cap)
    with mp_hands.Hands( max_num_hands=1,min_detection_confidence=0.5, min_tracking_confidence=0.5) as hands: 
        sequence = []
        for seq in range(3):
            # Loop through video length aka sequence length
            for frame_num in range(30):

                # Read feed
                ret, frame = cap.read()
                
                #print(frame)
                if ret==True:
                # Make detections
                    frame= imutils.resize(frame, width=520, height=420)
                    image, results = mediapipe_detection(frame, hands)
                    #print(image)

                    # Draw landmarks
                    draw_styled_landmarks2(image, results)

                    # NEW Apply wait logic
                    if frame_num == 0: 
                        cv2.rectangle(image, (0,0), (640, 40), (245, 117, 16), -1)
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32), 
                                                           cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)

                    # Show to screenq
                        cv2.imshow('OpenCV Feed', image)
                        #cv2.waitKey(1000)
                    else: 
                        cv2.putText(image, 'Collecting frames for {}'.format(seq), (25,32),cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                        # Show to screen
                        cv2.imshow('OpenCV Feed', image)

                    # NEW Export keypoints
                    #print(results.multi_hand_landmarks)
                    keypoints = extract_keypoints2(results)
                    print(keypoints)
                    npy_path = os.path.join('testAtoz', str(seq))
                    np.save(npy_path, keypoints)

                    # Break gracefully
                    if cv2.waitKey(15) & 0xFF == ord('q'):
                        break

    cap.release()
    cv2.destroyAllWindows()
    for frame_num in range(3):
        res = np.load(os.path.join('testAtoz', "{}.npy".format(frame_num)))
        #print(np.array(res).size)
        sequence.append(res)
        #print(window)

    #print(sequences)

    res = modelAtOZ.predict(np.expand_dims(sequence, axis=0))[0]
    print(actions2[np.argmax(res)])
    predictions.append(np.argmax(res))
    return actions2[np.argmax(res)]


# Creating a Web App
app = Flask(__name__)

# Creating an address for the node on Port 5000
node_address = str(uuid4()).replace('-', '')




# Adding a new transaction to the Blockchain
@app.route('/predict', methods = ['POST'])
def upload():
    if "video" in request.files:
        videofile = request.files["video"]
        videofile.save(videofile.filename)
        print(videofile)
        return jsonify(ValuePredictor(videofile.filename)), 201
    
# Adding a new transaction to the Blockchain
@app.route('/Atoz', methods = ['POST'])
def upload3():
    if "video" in request.files:
        videofile = request.files["video"]
        videofile.save(videofile.filename)
        print(videofile)
        return jsonify(ValuePredictor2(videofile.filename)), 201
      

@app.route('/', methods = ['GET'])
def upload2():
    
    return jsonify('Hello'), 201



# Running the app
app.run(host = 'localhost', port = 5000)

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://localhost:5000/ (Press CTRL+C to quit)


<FileStorage: 'nametest' ('video/mp4')>
nametest
[ 4.89949316e-01  4.30430591e-01 -9.72305894e-01  9.99902487e-01
  5.17288864e-01  3.98869097e-01 -9.10571218e-01  9.99795139e-01
  5.33343017e-01  4.01645064e-01 -9.10553336e-01  9.99821126e-01
  5.46460748e-01  4.04279232e-01 -9.10460770e-01  9.99808013e-01
  4.69745517e-01  3.93091857e-01 -9.06777859e-01  9.99752223e-01
  4.54746276e-01  3.91796291e-01 -9.07142401e-01  9.99761522e-01
  4.38821435e-01  3.90461922e-01 -9.06953692e-01  9.99771893e-01
  5.66926360e-01  4.32300568e-01 -5.18871069e-01  9.99777853e-01
  4.19075996e-01  4.13896084e-01 -4.94347960e-01  9.99650359e-01
  5.19022644e-01  4.78165448e-01 -8.23422432e-01  9.99952674e-01
  4.55675572e-01  4.70390975e-01 -8.17404747e-01  9.99949336e-01
  6.54539883e-01  6.78906918e-01 -3.58447611e-01  9.99902487e-01
  3.02909732e-01  6.54086053e-01 -3.22650969e-01  9.99821126e-01
  7.05030262e-01  9.42398548e-01 -2.93881506e-01  5.89811206e-01
  2.22720399e-01  9.44172740e-01 -2.11283

[ 4.90927786e-01  4.31339890e-01 -1.02546763e+00  9.99893248e-01
  5.17467201e-01  3.99154007e-01 -9.60488141e-01  9.99771595e-01
  5.33763409e-01  4.01737154e-01 -9.60565448e-01  9.99797583e-01
  5.46903312e-01  4.04261649e-01 -9.60470140e-01  9.99782920e-01
  4.69823182e-01  3.94349962e-01 -9.60068405e-01  9.99731719e-01
  4.54766572e-01  3.93598914e-01 -9.60436106e-01  9.99741912e-01
  4.38783675e-01  3.92769992e-01 -9.60355878e-01  9.99756932e-01
  5.68205237e-01  4.31902289e-01 -5.52892864e-01  9.99749601e-01
  4.19089019e-01  4.17395979e-01 -5.45085728e-01  9.99644756e-01
  5.21698594e-01  4.78739917e-01 -8.71036351e-01  9.99948442e-01
  4.57993925e-01  4.72864807e-01 -8.69432092e-01  9.99946296e-01
  6.58424735e-01  6.80182636e-01 -3.68402302e-01  9.99886096e-01
  3.03031027e-01  6.54018879e-01 -3.77949029e-01  9.99820650e-01
  7.02936530e-01  9.47807491e-01 -3.13166082e-01  5.91127396e-01
  2.20895767e-01  9.44693446e-01 -2.86450684e-01  5.60596824e-01
  7.07955599e-01  1.20401

[ 4.89746481e-01  4.31607217e-01 -1.02415264e+00  9.99886990e-01
  5.16516685e-01  3.99537921e-01 -9.60181534e-01  9.99758005e-01
  5.33259034e-01  4.02101308e-01 -9.60276246e-01  9.99782920e-01
  5.46356797e-01  4.04484123e-01 -9.60216224e-01  9.99767303e-01
  4.69183743e-01  3.94826889e-01 -9.59010243e-01  9.99722362e-01
  4.53858227e-01  3.94120634e-01 -9.59341645e-01  9.99733090e-01
  4.37348336e-01  3.93237203e-01 -9.59236026e-01  9.99750733e-01
  5.67912698e-01  4.32082385e-01 -5.55900693e-01  9.99732137e-01
  4.18278605e-01  4.18113828e-01 -5.44505894e-01  9.99649942e-01
  5.20571411e-01  4.78984326e-01 -8.70963097e-01  9.99944448e-01
  4.56669927e-01  4.73354787e-01 -8.68310094e-01  9.99943554e-01
  6.59029484e-01  6.80514753e-01 -3.74413401e-01  9.99863863e-01
  3.02937925e-01  6.53893948e-01 -3.73897314e-01  9.99814570e-01
  7.01946616e-01  9.47244108e-01 -3.15759510e-01  5.93833685e-01
  2.19922543e-01  9.44393098e-01 -2.80413419e-01  5.86029649e-01
  7.12859511e-01  1.19406

...

[ 5.44204056e-01  4.54488248e-01 -4.29683626e-01  9.99976814e-01
  5.56145966e-01  4.27718401e-01 -3.85007679e-01  9.99923885e-01
  5.67013860e-01  4.27483022e-01 -3.85322154e-01  9.99902964e-01
  5.75724244e-01  4.27151322e-01 -3.85253578e-01  9.99899149e-01
  5.21452308e-01  4.30707753e-01 -3.84094864e-01  9.99926627e-01
  5.09126127e-01  4.32566673e-01 -3.84006470e-01  9.99930382e-01
  4.96591389e-01  4.34672594e-01 -3.84016186e-01  9.99939978e-01
  5.87089300e-01  4.43223059e-01 -1.09187983e-01  9.99929667e-01
  4.79784071e-01  4.54155087e-01 -1.01248346e-01  9.99913573e-01
  5.68647146e-01  4.84367430e-01 -3.25645804e-01  9.99983668e-01
  5.22529781e-01  4.87024605e-01 -3.24109524e-01  9.99972403e-01
  6.63291693e-01  6.10117257e-01 -5.09260641e-03  9.99940872e-01
  3.97206753e-01  6.09704137e-01 -4.08881530e-02  9.99953985e-01
  7.27397263e-01  8.31227422e-01  1.67819019e-02  7.23215818e-01
  2.52400726e-01  7.64389157e-01 -3.57362807e-01  9.76911366e-01
  7.32521653e-01  1.02036

[ 5.44218779e-01  4.54499125e-01 -4.27795202e-01  9.99976814e-01
  5.56215107e-01  4.27733898e-01 -3.83193314e-01  9.99923587e-01
  5.67104399e-01  4.27498728e-01 -3.83524090e-01  9.99902427e-01
  5.75807810e-01  4.27172512e-01 -3.83458465e-01  9.99899149e-01
  5.21489441e-01  4.30715472e-01 -3.81863743e-01  9.99926388e-01
  5.09168684e-01  4.32569802e-01 -3.81787509e-01  9.99929965e-01
  4.96637672e-01  4.34657425e-01 -3.81802827e-01  9.99939799e-01
  5.87454617e-01  4.43240494e-01 -1.08321622e-01  9.99929368e-01
  4.79902059e-01  4.54115242e-01 -9.74642709e-02  9.99912202e-01
  5.68693638e-01  4.84374970e-01 -3.24344158e-01  9.99983728e-01
  5.22550583e-01  4.87036914e-01 -3.22306961e-01  9.99972343e-01
  6.63945377e-01  6.10148013e-01 -5.42654702e-03  9.99942899e-01
  3.98214519e-01  6.09323144e-01 -3.69580798e-02  9.99954700e-01
  7.28921652e-01  8.31410944e-01  1.59082413e-02  7.19064474e-01
  2.53191411e-01  7.64345825e-01 -3.53477865e-01  9.75477636e-01
  7.41662860e-01  1.02168

[ 5.44218779e-01  4.54499125e-01 -4.27795202e-01  9.99976814e-01
  5.56215107e-01  4.27733898e-01 -3.83193314e-01  9.99923587e-01
  5.67104399e-01  4.27498728e-01 -3.83524090e-01  9.99902427e-01
  5.75807810e-01  4.27172512e-01 -3.83458465e-01  9.99899149e-01
  5.21489441e-01  4.30715472e-01 -3.81863743e-01  9.99926388e-01
  5.09168684e-01  4.32569802e-01 -3.81787509e-01  9.99929965e-01
  4.96637672e-01  4.34657425e-01 -3.81802827e-01  9.99939799e-01
  5.87454617e-01  4.43240494e-01 -1.08321622e-01  9.99929368e-01
  4.79902059e-01  4.54115242e-01 -9.74642709e-02  9.99912202e-01
  5.68693638e-01  4.84374970e-01 -3.24344158e-01  9.99983728e-01
  5.22550583e-01  4.87036914e-01 -3.22306961e-01  9.99972343e-01
  6.63945377e-01  6.10148013e-01 -5.42654702e-03  9.99942899e-01
  3.98214519e-01  6.09323144e-01 -3.69580798e-02  9.99954700e-01
  7.28921652e-01  8.31410944e-01  1.59082413e-02  7.19064474e-01
  2.53191411e-01  7.64345825e-01 -3.53477865e-01  9.75477636e-01
  7.41662860e-01  1.02168

127.0.0.1 - - [30/Mar/2022 13:17:36] "POST /predict HTTP/1.1" 201 -


Hello
